In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!pip install firebase_admin
!pip install tqdm

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
import tqdm
from tqdm import tqdm
import firebase_admin
from firebase_admin import credentials,firestore
import re
from collections import defaultdict
import os
import json
from collections import defaultdict
import nltk
from nltk.corpus import stopwords
import string


Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
# Only run once
# /content/drive/Shareddrives/Annota/NLP AI/Data/lqa-prod-firebase-adminsdk-89kpr-d05bec9a4e.json
cd = credentials.Certificate("/content/drive/Shareddrives/Annota/NLPAI/Data/lqa-prod-firebase-adminsdk-89kpr-d05bec9a4e.json")

firebase_admin.initialize_app(cd)

datab = firestore.client()

First, we generate raw transcripts, with just the text.

In [ ]:
# Pull transcripts into transcript dict
db_transcripts = datab.collection(u'transcripts')
docs = db_transcripts.stream()

transcripts = {}
raw_transcripts = dict()
id_to_name = {}
for doc in docs:
    raw_transcripts[doc.to_dict()["interviewee"]] = doc.to_dict()
    transcripts[doc.id] = doc.to_dict()
    id_to_name[doc.id] = doc.to_dict()["interviewee"].strip()

In [ ]:
raw_transcripts["Jessica Santos"]["rawText"]

'BACKGROUND AND INTRODUCTIONSInterviewer 1  0:04  I do want to start by sharing a little bit about your background, especially as how you\'re related to your involvement to YFIOB.Jessica Santos  0:19  Yeah, so I work for Santa Cruz city schools district. I am the Director of Curriculum Instruction for grades six through 12. And I have known your futures our business for a while now, at first peripherally. I\'ve worked for a district for 11 years. And I started out as an assistant principal, and then became a principal of Mission Hill Middle School. And that\'s when I was first introduced to your future is our business was when I worked for Mission Hill. And I know your future is our business kind of helped set up some, not job, but career panels at our school, for maybe one or two years of the six years, I worked there. And I knew about them and knew they\'re out there. And then when I became the director of curriculum instruction, I started working with them a little bit more because 

In [ ]:
names = list(raw_transcripts.keys())
#for keys in raw_transcripts["Jessica Santos"]:
#  print(keys, ":", raw_transcripts["Jessica Santos"][keys])
names.remove("Veronica Mars")
print(names)

['Jessica Santos', 'Ayesha', 'Deb and Sky and Barb', 'Chris', 'P01177', 'Marketing Chair', 'Jennifer', 'Sam and Julia', 'Cali Thunderbird', 'Crystal', 'Ben', 'Jacob', 'Jaya Power', 'Sky and Deb and Barb', 'Mike', 'Speaker 2', 'Jane Smith', 'Kalyana Martini', 'Camille', 'P84631', 'Colson Foster', 'P39904', 'Samantha', 'Lisa MacDonald', 'Jane Doe', 'Alexis', 'Thomas Cao', 'P6643', 'Oda Power', 'Aaron Rush', 'P81489', 'Victor Clayton', 'David Ayers', 'Nellie Sky', 'John Smith', 'Jay', 'Interviewee', 'Edith Stacy', 'Livia Patrick', 'Emma McCarthy', 'Zeger and Mary and Manny', 'P44034', 'Katsu Sun', 'Nathan Porter', 'Xiulan Al-Hashim', 'Isobel', 'Guanyu', 'Kate Ollison', 'P66821', 'P58126', 'Uma Rose', 'P43832', 'Jenny May', 'P17221', 'Sierra Snow', 'Irene', 'Donna and Bobby', 'P19673', 'Katie', 'David Lee', 'Karen Asherah', 'Justin', 'Guanyu Sun', 'Amelia Winton', 'Bell Maria', 'Linda', 'Alice', 'Gregory Ramirez', 'P98704', 'Mountain Doc', 'Sara']


Mostly Generalizable Code to collect Raw Transcripts into Dictionaries as was done before. Only current issue is that if name is mentioned somewhere in transcript, we are splitting by that mention also. Solution is to add a requirement of a subsequent time_stamp to it, but not sure how to do that yet.

In [ ]:
##Unfortunately, some of the people have the wrong interviewers listed

raw_transcripts["Jacob"]["interviewer"] = "Interviewer1 and Interviewer2"
raw_transcripts["Mountain Doc"]["interviewer"] = "Interviewer1 and Interviewer2"
raw_transcripts["Veronica Mars"]["interviewer"] = "Interviewer1 and Interviewer2"
raw_transcripts["Samantha"]["interviewer"] = "Interviewer 1 and Interviewer 2"
raw_transcripts["Jane Doe"]["interviewer"] = "Interviewer 1 and Interviewer 2"
raw_transcripts["Nellie Sky"]["interviewer"] = "Interviewer1 and Interviewer2"
raw_transcripts["Isobel"]["interviewer"] = "Interviewer 1 and Interviewer 2"
raw_transcripts["Irene"]["interviewer"] = "Interviewer 2 and Interviewer2 and Interviewer 1 and Interviewer1"
raw_transcripts["Katie"]["interviewer"] = "Interviewer1 and Interviewer2"

In [ ]:
raw_text = {interviewee:raw_transcripts[interviewee]["rawText"] for interviewee in names}
#Two main issues: How to extract headings (ALL CAPS) + How to split sentences by who spoke them

def extract_time(text: str):
  time_extraction_copy = text
  time = ""
  for i in range(1, len(time_extraction_copy) - 2):
    if time_extraction_copy[i] == ":" and isinstance(int(time_extraction_copy[i-1]), int) and isinstance(int(time_extraction_copy[i+1]), int) and isinstance(int(time_extraction_copy[i+2]), int):
      prev_whitespace = time_extraction_copy[i - 2 : i + 2].index(" ") + i - 2
      time = time_extraction_copy[prev_whitespace + 1:i + 3]
      break
      break
  return "".join(time).strip()

def remove_time(text:str):
  time_removal_copy = text
  time = ""
  i = 1
  #for i in range(1, len(time_removal_copy) - 2):
  while i < len(time_removal_copy) - 2 and i >= 1:
    if time_removal_copy[i] == ":" and isinstance(int(time_removal_copy[i-1]), int) and isinstance(int(time_removal_copy[i+1]), int) and isinstance(int(time_removal_copy[i+2]), int):
      prev_whitespace = time_removal_copy[i - 2 : i + 2].index(" ") + i - 2
      time = time_removal_copy[prev_whitespace + 1 : i + 3]
      time_removal_copy = time_removal_copy[0:prev_whitespace + 1] + time_removal_copy[i + 3: ]
    i+=1
  return "".join(time_removal_copy).strip()

def in_in(interview_names, text):
  for name in interview_names:
    for names in name.split():
      if names in text:
        return True
  return False

def time_in(text):
  if ":" not in text:
    return False
  colon_index = text.index(":")
  if colon_index >=2 and text[colon_index - 1].isdigit() and text[colon_index + 1].isdigit() and isinstance(int(text[colon_index + 2]), int):
    return True
  else:
    return False

dealt_with = ["Camille", "P01177", "P84631", "P39904", "Thomas Cao", "P81489", "John Smith", "Isobel", "P66821", "P58126", "P43832", "P19673"]
failures = set()
name_raw_text_dict = dict()
for name in names:
    topics = 0
    rel_data_dict = dict()
    rel_info = raw_transcripts[name]
    interviewers = raw_transcripts[name]["interviewer"].split(" and ")
    print("Interviewers: ", interviewers, ", Interviewees: ", rel_info["interviewee"])
    rel_data_dict["INTERVIEW INFORMATION"] = {"Interviewer": interviewers, "Interviewee": rel_info["interviewee"]}
    #text_list = raw_text[name].split("\\n\\n")
    text_list = re.split("\\\\n\\\\n|\\\\\\n\\\\\\n", raw_text[name])
    text_list = [tx for tx in text_list if len(tx.strip()) != 0]
    name_split = rel_info["interviewee"].split()
    delimiters = "("+str(name) + " [0-9]*:[0-9]*|" + str(name) + "  [0-9]*:[0-9]*|" + str(name) + "   [0-9]*:[0-9]*"
    for part_name in name_split:
      delimiters += part_name + " [0-9]*:[0-9]*|" + part_name + "  [0-9]*:[0-9]*|" + part_name + "   [0-9]*:[0-9]*"
    for interviewer in interviewers:
      delimiters += "|" + str(interviewer)  + " [0-9]*:[0-9]*|" + str(interviewer) + "  [0-9]*:[0-9]*|" + str(interviewer) + "   [0-9]*:[0-9]*"
      for part_interviewer in interviewer.split():
        delimiters += "|" + str(part_interviewer)  + " [0-9]*:[0-9]*|" + str(part_interviewer) + "  [0-9]*:[0-9]*|" + str(part_interviewer) + "   [0-9]*:[0-9]*"
    delimiters += "\W)"
    most_recent_key = "DEFAULT"
    most_recent_speaker = ""
    needs_caps = False
    if isinstance(rel_data_dict["INTERVIEW INFORMATION"]["Interviewee"], str):
      ppl_list = rel_data_dict["INTERVIEW INFORMATION"]["Interviewee"].split(" and ") + interviewers
    else:
      ppl_list = rel_data_dict["INTERVIEW INFORMATION"]["Interviewee"] + interviewers
    for index in range(len(text_list)):
      regex_split = re.split(delimiters, text_list[index])
      regex_split = [reg.strip() for reg in regex_split if reg.strip() != ""]
      for i in range(len(regex_split)): 
        if (regex_split[i].strip().isupper() and not time_in(regex_split[i].strip())) or (len(regex_split[i].strip().split()) <= 10 and not time_in(regex_split[i].strip()) and not needs_caps and not in_in(ppl_list, regex_split[i - 1].strip()) and not in_in(ppl_list, regex_split[i].strip()) and regex_split[i].strip()!="" and regex_split[i].strip()!="%p%"): #Checks if text is actually the Topic Name, in which case the rel_data_dict[topic] = topic_dict
          rel_data_dict[regex_split[i].strip()] = dict()
          most_recent_key = regex_split[i].strip()
          topics+=1
          print("Most Recent Key:", regex_split[i].strip())
          if regex_split[i].isupper() and name != "Nellie Sky":
            needs_caps = True
        elif in_in(ppl_list, regex_split[i].strip()) and time_in(regex_split[i].strip()): #Checks if text is actually the interviewer name, or interviewee name. The condition needs to use an in_in function, takes the text and the list of interviewers. If any listed interviewer is in the text, return true, else false.
          #most_recent_key = list(rel_data_dict.keys())[-1]
          try:
            if(most_recent_key not in rel_data_dict):
              rel_data_dict[most_recent_key] = dict()
            most_recent_speaker = regex_split[i].strip()
            rel_data_dict[most_recent_key][most_recent_speaker] = ""
            print("Most Recent Speaker:", most_recent_speaker)
          except:
            failures.add(name)
            assert name in dealt_with or False, name
        else:
          #most_recent_key = list(rel_data_dict.keys())[-1]
          print("speech: "+ regex_split[i].strip())
          if most_recent_key not in rel_data_dict.keys():
            rel_data_dict[most_recent_key] = dict()
          rel_data_dict[most_recent_key][most_recent_speaker] = regex_split[i].strip()
    name_raw_text_dict[name] = rel_data_dict
    if(topics==0 and name not in dealt_with):
      print(name)
print("FAILURES: ", len(failures), failures)

Streaming output truncated to the last 5000 lines.
speech: So that's been challenging. There's been a tremendous amount of learning. For me personally, and for people in the company the last year and a half, two years in the data science and machine learning space. finding qualified, affordable talent in the area is hugely difficult. The thing is, Facebook, you know, their median salary is 250,000 a year, and they bring in $650,000 in revenue per employee.
Most Recent Speaker: David Lee  14:25
speech: Wait how much?
Most Recent Speaker: John Smith  14:26
speech: 650,000 is in revenue per employee. Because they're a subscription service. Well, I mean, they're not a subscription there. They get all their ad revenue, right. So yeah, if I got paid $650,000 per person that worked for my company, it would be very easy for me to pay 250,000.
Most Recent Speaker: David Lee  14:48
speech: Yeah,
Most Recent Speaker: John Smith  14:48
speech: The rates that we can charge our customers don't allow

This code is used to check on transcripts that the code above doesn't correctly pick up the topics of.

In [ ]:
text_split = re.split("\\\\n\\\\n|\\\\\\n\\\\\\n|\\r", raw_transcripts["Isobel"]["rawText"])
delimiters = "(Katsu Sun  [0-9]*:[0-9]*|Annie Zhang  [0-9]*:[0-9]*\W)"
further_split = [re.split(delimiters, text) for text in text_split]
furthest_split = [text.strip() for split in further_split for text in split if text.strip() != ""]
furthest_split

["Interviewer 1 0:11  Okay, cool. Thank you. Um, could you start by telling us a little bit more about your background and interest in arts IV?Isobel  0:19  So I'm a mom with young kids. So I think for me before, I didn't do that much art, but now it's more looking into it for my kids.",
 "Interviewer 1 0:40  Can you describe the role of art in your life, when you're doing them with your kids, or looking for something to do?Isobel  0:50  Probably just to develop some kind of appreciation, or distributing in the world and different forms of how to create beauty. And I think that's probably the purpose for the gifts and also to learn some basic techniques that they can use in creating arts.",
 "Interviewer 1 1:16  And what kind of programs are you currently engaged in or have engaged in before with your kids?Isobel  1:25  And so my kids did something called animal arts where they basically do realistic drawing of different animals. And this is my older one. And then right now she's doing

In [ ]:
text_split = raw_transcripts["Veronica Mars"]["rawText"].split("\\n\\n")
print(len(text_split))
delimiters = "(Veronica Mars  |Interviewer1  |Interviewer2  \W)"
further_split = [re.split(delimiters, text) for text in text_split]
furthest_split = [text for split in further_split for text in split]
for text in furthest_split:
  print(text + "\n")

29
INTRODUCTION/EXPERIENCEInterviewer1Hey, hi. Okay, so just to let you know, I am recording the session already. So hi, I'm Interviewer1, I'm going to be doing half of your interview. And Interviewer2 over here is going to be also doing the other half.Interviewer2 So if it's okay with you, we can get started with the questions. Okay, so before we dive into your SCMAC experience, could you start by telling us a little bit about your background and your interest in the arts?

Veronica Mars  

Yeah. Okay, so I've lived in the Santa Cruz area for about nine years, I ended up transferring from a different college to go to UC Santa Cruz. And then I did a PhD in linguistics at Santa Cruz as well. I graduated in 2018. And then since then, I've been working in the tech world on the other side of the hill, but I live here in Santa Cruz. I live in Felton, actually. So I work as a linguist at Cisco currently. So linguistics is kind of an inherently creative field, even though it's kind of not mor

In [ ]:
split_transcript = raw_transcripts["Mountain Doc"]["rawText"].split("\\n\\n")
split_transcript = [re.split("(Interviewer1  [0-9]*:[0-9]*|Interviewer1 [0-9]*:[0-9]*|Interviewer2 [0-9]*:[0-9]*|Interviewer2  [0-9]*:[0-9]*|Mountain Doc [0-9]*:[0-9]*|Mountain Doc  [0-9]*:[0-9]*|Mountain Doc   [0-9]*:[0-9]*\W)", text) for text in split_transcript]
split_transcript = [text.strip() for split in split_transcript for text in split if text.strip()!= ""]
split_transcript

['Introduction/Artistic Background',
 'Interviewer1  0:00',
 "I'm sure you've already been introduced to Interviewer2. So I'll be taking over the first half of your interview and Interviewer2 will be taking over the second half. Do you have any questions before we start?",
 'Mountain Doc  0:13',
 "I don't. I hope I can be helpful. I'm not like a frequent patron of that place. But yeah.",
 'Interviewer1  0:22',
 'All experience is important here. Okay. So before we dive into anything about the Santa Cruz Mountains Art Center could you start by telling us a little bit about your background and interest in the arts?',
 'Mountain Doc  0:37',
 "In the arts? Yeah. Okay. Well, um, my son took a class they offered at the local elementary school, maybe a year and a half ago. So I had, like, emailed them to see if they're going to get that going. And then somehow that kind of signed me up for this, but my husband's into art, and they do art. We do art with the kids, you know, like drawing, I'm m

The raw transcripts have been successfully (I think) collected into the name_raw_text_dict. Now we just have to collect annotations.

In [ ]:
name_raw_text_dict

{'Aaron Rush': {'//BACKGROUND': {'Aaron Rush  0:15': "My involvement, is to get involved in actually getting women in technology. It is, you know, I'm not going to quote the numbers because you know, and the sad thing is young ladies, when you get in the industry, no matter how many PhDs you have, no matter how big your brain, you're always going to be fighting against the male set of the way things should be done away thinking should be done. And that is not the way of the world. So my objective is to work with young women. And so one of the things is upon retirement, I came up here and started volunteering. My wife and I, we volunteered as teachers in the jail system. These are just unfortunate people, men and women. I taught in a women's jail, who have not made necessarily the right choices. I am caurrently teaching at Cabrillo College. I teach computer information. This is more for a certificate based program, and I teach at PV USD as a substitute teacher. In fact, today, I taught 

In [ ]:
transcripts.keys()

dict_keys(['2D2OPdmmqj3GYAZxHlYl', '2a4r1i6rIBjScfUfW8Cl', '2oVrDMmS7Sn9H1tmYe76', '3h1HK69ltiCcArDOfpZB', '42RWH3P6FGfyZgm0W2f5', '4dACzd4dPltKJepYDttJ', '6Rpfxq4MCi7AdL5Rj8Ht', '7ilvvVVGtAYpQeyI9ClG', '89r5kGPMaMWVlVtI1oR5', '997vNTqZpPXw8cD5ee2K', 'AIuyQUwkV2W2XANmIuVk', 'AKZdnx8irtrOgpGlts8B', 'AjTEySmPtvdciWwDYd65', 'Bed3Rgz7xXRjZZdpnzAF', 'Bjx5dpWidyMxmixmUpzI', 'BtXOewR7xWQCu7AIgsni', 'C5aVrArd2pgoYKpYDpAw', 'DZkgPKNePKgM7OTZe4BG', 'DZyLNQM38jr937dJBBXi', 'EJMOoU83P3kFPHWGkWQ7', 'Ehq4KuDdp8I7Q98hsKTO', 'GCtUQ0guy8yuz3CBirlq', 'GJ2x1N3OJxIXYo8eYcyK', 'HhMIbL0oOf72gGN7koKJ', 'HtzlwmaGPTAFrCV4fk9e', 'I7e06YTfDwcBfSoNo003', 'IfyxRUznWVVsNNVWrlYh', 'IkKk6mQOpl1kY4BbmB1Q', 'JqmBwDY7Q1itcmrh0Pyg', 'KFvG0wjy9hVpJ0BLs0Qf', 'MUH64eem3po5j6thNibX', 'NP514u0teTkaX5oOMU5U', 'PAJGmcX1yfGiyuYwqhkE', 'PYUcEJkN4ligEW47OYu6', 'TpY75Dj1jAjXMSeNccRr', 'U6Jpuq2aERnBQgcZHA3e', 'VLo8gbvmFz0smPyxNWeu', 'VRUeyUbZHJjdBFTcpIdT', 'VdX0IqI9QgKjvNhzITXa', 'Vh4AIsBjjJiyu1VmQLU1', 'VszqGpncyEveBulkVHVB', 'W3da

In [ ]:
# Pull annotations into annotation dict
db_annotations = datab.collection(u'annotations')
docs = db_annotations.stream()

annotations = defaultdict(lambda: [])
for doc in docs:
    text_name = id_to_name[doc.to_dict()['__transcriptId']]
    annotations[text_name].append(doc.to_dict())
    print(doc.to_dict())

users = set()
for name in names:
  for annotation in annotations[name]:
    users.add(annotation["__userId"])

users = sorted(list(users))
id_to_user = {users[i]:i for i in range(len(users))}

Streaming output truncated to the last 5000 lines.
{'_createdAt': DatetimeWithNanoseconds(2022, 1, 6, 2, 2, 41, 146000, tzinfo=<UTC>), 'endingLine': 30, '_updatedAt': DatetimeWithNanoseconds(2022, 1, 7, 22, 58, 49, 202000, tzinfo=<UTC>), '__codeId': None, '__transcriptId': 'ps5jPbyUsFJ9IqD71nMt', '_selectionRange': '{"startTextIndex":39,"endTextIndex":39,"startOffset":0,"endOffset":27}', '_highlightedText': "I don't do it consistently.", '__id': 'NjbTjCXjlUfxnnvR0U1U', '__researchQuestionId': '1FPayvY7fCjoY2kRVzuU', '__userId': 'hdA8Z0nULYSG6NcC77q8HswDwbQ2', 'startingLine': 30, 'submitted': True, 'round': [True, True, True], 'annotationText': 'SD: lots of free time and fills it with art', 'isApproved': None, 'startingChar': 1634, 'endingChar': 1661}
{'_createdAt': DatetimeWithNanoseconds(2022, 1, 12, 2, 32, 5, 310000, tzinfo=<UTC>), '_updatedAt': DatetimeWithNanoseconds(2022, 1, 12, 2, 47, 6, 968000, tzinfo=<UTC>), 'endingChar': 9037, '_selectionRange': '{"startTextIndex":87,"endTextI

DeadlineExceeded: ignored

In [ ]:
dev_team = ["hffcbvyhiShIzci1l1QyANX4U5e2",
"heldKodTPHN0a07y0awqi0ZmRY12",
"fDbnwAxLtVa7hnNJXxFzwXUIGsi1",
"bB46zAGTCgR8nE2dn30Ac7VKDAZ2",
"Y5NEzmla82RutQ5GYLoxD5yU4Ao2",
"VptK2x2sZNXh1ML7WcbUfshnHJZ2",
"ScfL0hBBNxbgkQvTm92zwH00hFf1",
"QP6aQRb05ZUQxOVSsgRjPx4vf6E2",
"OFkek7ucxpTmRPQAsl3Rs6aChNB2",
"JNYzNQsuAXdDM8xkWo9iywQA32K3",
"H0T1LF7IocfYADkLObgE3PzGVY92",
"GAYi8IhoSsV40wkPCaBqAEXvXW23",
"B3OCXJ2mOLNmCCpQ4NkPAAJL7rw1",
"7nZxKKhsPaWdcjbbax5WmiPlQb13"]

for dev in dev_team:
  print(id_to_user.get(dev))

In [ ]:
annotations["Amelia Winton"][0]

In [ ]:
name = "Jessica Santos"
sents = []
anns = []

def in_part(part, whole):
  for text in whole:
    if part in text or text in part:
      return True, text, index
  return False, "", index

for i in range(len(annotations[name])):
  is_in, text, index = in_part(annotations[name][i]["_highlightedText"], sents)
  if is_in:
    print(annotations[name][i]["_highlightedText"])
    print(text)
    print()
  sents.append(annotations[name][i]["_highlightedText"])
  anns.append(annotations[name][i])

In [ ]:
annotations["Jessica Santos"][0]

In [ ]:
for name in names:
  ann = annotations[name]
  for i in range(len(ann)):
    annotations[name][i]["__userId"] = "ann0_" + str(id_to_user[ann[i]["__userId"]])

In [ ]:
annotations["Jessica Santos"][0].keys()

In [ ]:
id_to_rq = {}

In [ ]:
db_annotations = datab.collection(u'researchQuestions')
docs = db_annotations.stream()

research_elaboration = dict()
for doc in docs:
    doc_dict = doc.to_dict()
    #print(doc_dict["title"] + ": " + doc_dict["text"] + "\n")
    #print(doc_dict)
    research_elaboration[doc_dict["title"]] = doc_dict["text"].replace("“", "\'").replace("”", "\'")
    id_to_rq[doc_dict["__id"]] = doc_dict["title"] 
print(id_to_rq.keys())

with open("/content/drive/Shareddrives/Annota/NLPAI/Data/Phase2Data/rq_expanded.json", "w") as f:
  json.dump(research_elaboration, f)

dict_keys(['1FPayvY7fCjoY2kRVzuU', '2CJFHVLReliU4D8r3S14', '2IMlYANMhGCD13BCiDxg', '3NArej80cEvwZPUUQQjp', '7VzNPtL9hDKJGciM3UYn', '8o863WRKDsLPcGvnwcR3', 'HmZDizI4QCS87zzIQ9sK', 'MpbYXwwZzlRqOQPhlsjy', 'YdKQfKwSFIfozY3Vyya2', 'ZTS3AbFtvQhBDgV76v8J', 'e0NO2V6taxOI8cz3r8sn', 'kwOVsTa8LvwpD2deDEjt', 'ufXFKMMnLi1Z8l5SJXmK'])


In [ ]:
def str_to_dict(dict_str: str):
  count = dict_str.count(":")
  dict_str = dict_str.replace("{", "")
  dict_str = dict_str.replace("}", "")
  dict_str = dict_str.replace("\"", "")
  dict_str = dict_str.replace("\'", "")
  result_dict = dict()
  if count == 0:
    return dict()
  else:
    str_list = re.split(":|,", dict_str) #dict_str.split(":")
    for i in range(len(str_list)):
      if i%2 == 0:
        result_dict[str_list[i]] = ""
      else:
        result_dict[str_list[i-1]] = str_list[i]
  return result_dict

In [ ]:
db_annotations = datab.collection(u'transcriptLines')
docs = db_annotations.stream()
importance_dict = dict()
for doc in docs:
  if "importance" in doc.to_dict().keys():
    doc_dict = doc.to_dict()
    imp_dict = str_to_dict(doc_dict["importance"])
    text = doc_dict["text"].replace("\\n", "").replace("\"", "").replace("\\", "").strip()
    if text == "" or id_to_name[doc_dict['__transcriptId']] == "Interviewee":
      continue
    loc_imp_dict = {id_to_rq[k]:imp_dict[k] for k in imp_dict.keys()}
    if id_to_name[doc_dict["__transcriptId"]] in importance_dict.keys():
      importance_dict[id_to_name[doc_dict["__transcriptId"]]][text] = loc_imp_dict
    else:
      importance_dict[id_to_name[doc_dict["__transcriptId"]]] = dict()
      importance_dict[id_to_name[doc_dict["__transcriptId"]]][text] = loc_imp_dict

grader_annotations = importance_dict

In [ ]:
graded = grader_annotations.keys()
with open("/content/drive/Shareddrives/Annota/NLPAI/Data/Phase2Misc/graded.json", "w") as f:
  json.dump(list(graded), f)

In [ ]:
def search(haystack, needle):
  max_overlap = 0
  max_index = -1
  for hay_number in range(len(haystack)):
    hay = haystack[hay_number]["text"]
    overlap = get_overlap(hay, needle)
    if(overlap > max_overlap and overlap >=3):
      max_overlap = overlap
      max_index = hay_number
  if(max_overlap >= 3):
    return max_index
  else:
    return -1

In [ ]:
annotators = set()
for name_index in (range(len(names))):
  name = names[name_index]
  ann = annotations[name]
  for i in range(len(ann)):
    annotators.add(ann[i]["__userId"])

len(annotators)

240

In [ ]:
nltk.download('stopwords')

nltk.download('punkt')
PUNCT_REMOVE = string.punctuation

def get_overlap(sent1,sent2):
  stop_words = set(stopwords.words('english'))
  PUNCT_REMOVE = string.punctuation

  sent1=sent1.translate(str.maketrans('', '', PUNCT_REMOVE))
  sent2=sent2.translate(str.maketrans('', '', PUNCT_REMOVE))
  s1=nltk.word_tokenize(sent1)
  
  s2=nltk.word_tokenize(sent2)
  s1=[t for t in s1 if t.lower() not in stop_words]
  s2=[t for t in s2 if t.lower() not in stop_words]
  if len(s1)>=2:
    b1=nltk.bigrams(s1)
    s1=set([t for t in b1])
  else:
    s1=set(s1)
  if len(s2)>=2:
    b2=nltk.bigrams(s2)
    s2=set([t for t in b2])
  else:
    s2=set(s2)
  return len(s1 & s2)
  
ann_data_dict = dict()
for name_index in tqdm(range(len(names))):
  name = names[name_index]
  if name != "Guanyu Sun":
    continue
  ann_data_dict[name] = []
  ann = annotations[name]
  for i in range(len(ann)):
    text = ann[i]["_highlightedText"]
    found_key = ""
    max_overlap = 0

    for sent_index in range(len(ann_data_dict[name])):
      sent = ann_data_dict[name][sent_index]
      #print(sent)
      key = sent["text"]
      if(get_overlap(key, text) > max_overlap and get_overlap(key, text) >= 3):
        found_key = sent_index
        max_overlap = get_overlap(key, text)
    ann_data = {"id": ann[i]["__userId"],\
                "ResearchQuestionId": id_to_rq[ann[i]["__researchQuestionId"]],\
                "text": ann[i]["annotationText"]}
    if max_overlap >= 3:
      
      try:
        #print(ann_data_dict[name][found_key]["text"])
        ann_data_dict[name][found_key]["count"] += 1
        ann_data_dict[name][found_key]["annotations"].append(ann_data)
      except:
        print("Found_Index: ", found_key)
        assert False
    else:
      ann_data_dict[name].append(dict())
      ann_data_dict[name][-1]["text"] = text
      ann_data_dict[name][-1]["count"] = 1
      ann_data_dict[name][-1]["annotations"] = [ann_data]

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


100%|██████████| 71/71 [02:24<00:00,  2.03s/it]


In [ ]:
ann_data_dict

{'Guanyu Sun': [{'annotations': [{'ResearchQuestionId': 'Opportunities, Threats, PEST, Competition',
     'id': 'ann0_45',
     'text': 'O-great opportunity to gain knowledge and experience for benefit in future'}],
   'count': 1,
   'text': ' The mock interviews are fun, too.'},
  {'annotations': [{'ResearchQuestionId': 'Values',
     'id': 'ann0_136',
     'text': 'partnerships with other groups'},
    {'ResearchQuestionId': 'Opportunities, Threats, PEST, Competition',
     'id': 'ann0_145',
     'text': 'T (Competition) - Organizations that have the similar purposes and programs'},
    {'ResearchQuestionId': 'Opportunities, Threats, PEST, Competition',
     'id': 'ann0_107',
     'text': 'C - Competition - National organization vs county organization'},
    {'ResearchQuestionId': 'Opportunities, Threats, PEST, Competition',
     'id': 'ann0_52',
     'text': 'There is threat from competitors, however in this case, when the work they do is for the students and children, I do not thin

In [ ]:
for name in names:
  if name not in grader_annotations.keys():
    continue

  graded_transcript = grader_annotations[name]

  for k in graded_transcript.keys(): #This is going to be a sentence, we need to find it in the ann_data_dict, and add something for it
    index = search(ann_data_dict[name], k)
    if index >= 0:
      ann_data_dict[name][index]["grader_annotations"] = graded_transcript[k]

In [ ]:
for name in names:
  with open("/content/drive/Shareddrives/Annota/NLPAI/Data/Phase2Data/" + name + ".json", "w") as f:
    json.dump(ann_data_dict[name], f)

In [ ]:
ann_data_dict["Jessica Santos"]

defaultdict(list,
            {" And I think it's because also the federal government requires states to do monitoring to make sure you have a high quality CTE program.": [{'ResearchQuestionId': 'Background',
               'id': 'ann0_116',
               'text': 'Background-Environment-Federally Funded'}],
             " And it's not just a work portfolio that showcases student work. But it also includes things like a resume, job applications that are filled out, and other work based learning type components in there. And so you do that if you're in a CTE class, that's just one of the requirements. All of our CTE classes also include the Career Ready practice standards.": [{'ResearchQuestionId': 'Experience',
               'id': 'ann0_171',
               'text': 'positive-Access to Resources'}],
             ' And so as I learned, really, it was Mary Gaukel, who I started connecting with and realized she was a great resource for me, and she was a big part of your future is our busi

In [ ]:
keys = list(ann_data_dict["Jessica Santos"].keys())
ann_data_dict["Jessica Santos"][keys[0]][0]

{'__codeId': None,
 '__id': '02NG1OoeWUjf5xdN75NT',
 '__researchQuestionId': 'YdKQfKwSFIfozY3Vyya2',
 '__transcriptId': '2D2OPdmmqj3GYAZxHlYl',
 '__userId': 116,
 '_createdAt': DatetimeWithNanoseconds(2022, 4, 22, 4, 26, 49, 536000, tzinfo=<UTC>),
 '_highlightedText': "And then the COE has also been doing an IT essentials pathway which we're going to have a lot of kids taking advantage of coming up this school year. We have a huge digital arts or arts media entertainment program, we have digital Photography pathway, we have a graphic design pathway. And we also have a what is it? Like Film Video Production pathway? We have a lot of different CTE programs that we have over 3000 high school students in our district, and every year we have between 1300-1400 students taking the CTE classes.",
 '_selectionRange': '{"startTextIndex":40,"endTextIndex":40,"startOffset":1064,"endOffset":1591}',
 '_updatedAt': DatetimeWithNanoseconds(2022, 4, 22, 7, 53, 45, 999000, tzinfo=<UTC>),
 'annotationTex

In [ ]:
name = "Chris"
def in_part(part, whole):
  for text in whole:
    if part in whole or whole in part:
      return True
  return False

for ann in annotations[name]:
  print(ann["_highlightedText"])

 So there are five of us, that are sort of a steering committee, and we do different things.
cost effective
if we can start implementing some things that bring in more people and bring in more revenue, and bring in more students and bring in, you know, all of that stuff,
So, so we like to be seen as a part of the community, and that we're offering valuable services to the community. And something that people enjoy and value.
only one in our area
we have one part time employee, and that's all and volunteers are great.
finding ways to attract more teachers
 think most of the people there have had a good experience. And we feel like we're we're working towards something that's, that's a benefit to all of us and to the community. And that's kind of nice. And so that kind of starts creating these bonds. And then we do things together that are fun, and that we enjoy. Like, both of the people who were originally in charge of the ceramic studio when I started, I have taken my class. You know?


In [ ]:
# Build list of annotated transcripts
annotated_transcripts = []
for transcript_id in transcripts.keys():
    annotated_transcripts.append({"cleaned_transcript": name_raw_text_dict[id_to_name[transcript_id]],
                                  "raw_transcript": transcripts[transcript_id],
                            "annotations":annotations[transcript_id]})

# annotated_transcripts is a list of dictionaries with the keys "transcript" and
# "annotations". "transcript" yields the database dictionary for a given
# transcript, and "annotations" yields a list of all annotations (represented as
# dicts) for the current transcript

print(annotated_transcripts[0])

{'cleaned_transcript': {'INTERVIEW INFORMATION': {'Interviewer': ['Interviewer 1', 'Interviewer 2'], 'Interviewee': 'Jessica Santos'}, 'BACKGROUND AND INTRODUCTIONS': {'Interviewer 1  0:04': "I do want to start by sharing a little bit about your background, especially as how you're related to your involvement to YFIOB.", 'Jessica Santos  0:19': "Yeah, so I work for Santa Cruz city schools district. I am the Director of Curriculum Instruction for grades six through 12. And I have known your futures our business for a while now, at first peripherally. I've worked for a district for 11 years. And I started out as an assistant principal, and then became a principal of Mission Hill Middle School. And that's when I was first introduced to your future is our business was when I worked for Mission Hill. And I know your future is our business kind of helped set up some, not job, but career panels at our school, for maybe one or two years of the six years, I worked there. And I knew about them a

In [ ]:
annotations_list[0]

{'__codeId': None,
 '__id': '0klKZIhCd0p6z6QQNv7B',
 '__researchQuestionId': '3NArej80cEvwZPUUQQjp',
 '__transcriptId': '3h1HK69ltiCcArDOfpZB',
 '__userId': 'w1WdA9Mwwqa9qRJlyC667rpskgT2',
 '_createdAt': DatetimeWithNanoseconds(2021, 10, 25, 17, 54, 5, 994000, tzinfo=<UTC>),
 '_highlightedText': ' So there are five of us, that are sort of a steering committee, and we do different things.',
 '_selectionRange': '{"startTextIndex":29,"endTextIndex":29,"startOffset":500,"endOffset":592}',
 '_updatedAt': DatetimeWithNanoseconds(2021, 10, 25, 18, 9, 15, 845000, tzinfo=<UTC>),
 'annotationText': 'team- working together in different roles to manage the committee',
 'endingChar': 592,
 'endingLine': 36,
 'isApproved': None,
 'round': [True, True],
 'startingChar': 500,
 'startingLine': 36,
 'submitted': True}

In [ ]:
import pandas as pd
data = pd.read_csv('/content/drive/Shareddrives/Annota/NLP AI/Data/Chris_Quotes_per_single_sentence.csv')

data_text = data['Quotes']
print(len(data_text))
docs = data_text.tolist()
print(docs)

In [ ]:
# issue: users highlight text cross sentences, 
# need to account the sentences highlighted like this(original text: "This is the first sentence. This is the second sentence"): 
# highlight: "is the first sentence. This is the second"
freq_dict = dict()
atleastOne = 0
for doc in docs:
  freq_dict[doc] = 0
  for annotation in annotations_list:
     if annotation['__userId'] == 'heldKodTPHN0a07y0awqi0ZmRY12':
       if annotation['__researchQuestionId'] == 'MpbYXwwZzlRqOQPhlsjy':
        if doc in annotation['_highlightedText'] or annotation['_highlightedText'] in doc:
          freq_dict[doc]+=1
      
# sentences with at least 2 annotations has label 1, otherwise label is 0  
for key in freq_dict:
  if freq_dict[key]>=1:
    atleastOne +=1
    freq_dict[key] = 1
  else:
    freq_dict[key] = 0


print(freq_dict)
print('number of annotations:', len(annotations_list))
print("number of sentences:", len(docs))

print("freq_dict length", len(freq_dict))
print("number of sentences with at least 1 annotations", atleastOne)

In [ ]:
if 'And I was so happy about that.' in 'we want to raise our veil visible I can say it really I can visibility':
  print('1true')

if 'we want to raise our veil visible I can say it really I can visibility' in 'And I was so happy about that.':
  print('2true')